## Technical Indicators List

All the indicators that https://pypi.org/project/stockstats/ supports

In [1]:
INDICATORS_LIST_ALL = ['high_5_sma','rsi','boll','macd','cr','wr','cci','tr','atr','dma','pdi','dx','adx','adxr','trix','tema','vr','mfi','vwma',
                   'chop','ppo','stochrsi','supertrend','aroon','close_75_z','ao'
                   ]

The goal is to come up with an optimal combination of technical indicators for stock trading, automating the whole process with a DRL Agent.

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
#%matplotlib inline
import mplfinance as mpf # matplot.finance to plot candlesticks
import random
import itertools # iterators for efficient looping: https://docs.python.org/3/library/itertools.html 

from finrl.meta.preprocessor.yahoodownloader import YahooDownloader # a veces puede dar error al hacer fetch de la data porque no encuentra un stock o sus precios, o por la timezone
from finrl import config_tickers # config_tickers es una clase en la que se guardan en listas los nombres de cada stock para cada índice
from finrl.meta.preprocessor.preprocessors import FeatureEngineer, data_split
from finrl.meta.env_stock_trading.env_stocktrading import StockTradingEnv
from finrl.agents.stablebaselines3.models import DRLAgent
from stable_baselines3.common.logger import configure
from finrl.plot import backtest_stats, backtest_plot, get_daily_return, get_baseline

/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/pyfolio/pos.py:26: UserWarning: Module "zipline.assets" not found; mutltipliers will not be applied to position notionals.
  warnings.warn(


(podemos hacer pruebas para evitar crisis)

In [3]:
TRAIN_START_DATE = '2010-01-01'
TRAIN_END_DATE = '2021-10-01'
TEST_START_DATE = '2021-10-01'
TEST_END_DATE = '2023-03-01'

In [4]:
stock = YahooDownloader(start_date = TRAIN_START_DATE,
                     end_date = TEST_END_DATE,
                     ticker_list = config_tickers.DOW_30_TICKER).fetch_data()

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  1 of 1 completed
[*********************100%%*******

Shape of DataFrame:  (97013, 8)


In [5]:
stock # this DF contains all the stock price history from the train start date to the test end date, for every firm in the DJ30

date        open        high         low       close     volume  \
0      2010-01-04    7.622500    7.660714    7.585000    6.461978  493729600   
1      2010-01-04   56.630001   57.869999   56.560001   41.200783    5277400   
2      2010-01-04   40.810001   41.099998   40.389999   33.090416    6894300   
3      2010-01-04   55.720001   56.389999   54.799999   43.777565    6186700   
4      2010-01-04   57.650002   59.189999   57.509998   40.190220    7325600   
...           ...         ...         ...         ...         ...        ...   
97008  2023-02-28  482.670013  483.359985  473.920013  465.066833    3902100   
97009  2023-02-28  220.000000  221.770004  219.500000  217.824539    5385400   
97010  2023-02-28   38.700001   38.970001   38.549999   35.538383   16685300   
97011  2023-02-28   35.480000   35.779999   35.320000   32.750980    8847000   
97012  2023-02-28   47.000000   47.549999   46.983334   46.346081   18054000   

        tic  day  
0      AAPL    0  
1      AMGN    0  
2       AXP    0  
3        BA    0  
4       CAT    0  
...     ...  ...  
97008   UNH    1  
97009     V    1  
97010    VZ    1  
97011   WBA    1  
97012   WMT    1  

[97013 rows x 8 columns]

In [6]:
stock.day.describe()

count    97013.000000
mean         2.024131
std          1.398530
min          0.000000
25%          1.000000
50%          2.000000
75%          3.000000
max          4.000000
Name: day, dtype: float64

Stock symbols

In [7]:
tickers = stock.tic.unique()

Sometimes, for some tickers, some stocks are unavailable because of unavailable timezone or price data from YahooFinance

We wanted to get:

In [8]:
print(np.reshape(config_tickers.DOW_30_TICKER, (len(config_tickers.DOW_30_TICKER))))
print("Number of firms in the index: ",len(config_tickers.DOW_30_TICKER))

['AXP' 'AMGN' 'AAPL' 'BA' 'CAT' 'CSCO' 'CVX' 'GS' 'HD' 'HON' 'IBM' 'INTC'
 'JNJ' 'KO' 'JPM' 'MCD' 'MMM' 'MRK' 'MSFT' 'NKE' 'PG' 'TRV' 'UNH' 'CRM'
 'VZ' 'V' 'WBA' 'WMT' 'DIS' 'DOW']
Number of firms in the index:  30


But we got (because of the unavailable timezone or price data):

In [9]:
print(tickers) # stocks we have to train the agent
print("Number of firms downloaded: ",len(tickers))

['AAPL' 'AMGN' 'AXP' 'BA' 'CAT' 'CRM' 'CSCO' 'CVX' 'DIS' 'GS' 'HD' 'HON'
 'IBM' 'INTC' 'JNJ' 'JPM' 'KO' 'MCD' 'MMM' 'MRK' 'MSFT' 'NKE' 'PG' 'TRV'
 'UNH' 'V' 'VZ' 'WBA' 'WMT' 'DOW']
Number of firms downloaded:  30


Let's plot the stock opening prices for every company over the period we defined, in order to see the evolution and generate an idea of the optimal strategy.

In [10]:
stock_data = stock.drop(columns=['day']).copy(deep=True) # independent copy with dates, prices, volumes and stock symbol (company)
stock_data['date'] = pd.to_datetime(stock_data['date']) # convert date to type date
stock_data_training = stock_data[stock_data['date'] < TEST_START_DATE]
stock_data_testing = stock_data[stock_data['date'] >= TEST_START_DATE]
stock_data.set_index('date', inplace=True) # set column date as index
stock_data_training.set_index('date', inplace=True)
stock_data_testing.set_index('date', inplace=True)

In [11]:
stock_data

open        high         low       close     volume   tic
date                                                                       
2010-01-04    7.622500    7.660714    7.585000    6.461978  493729600  AAPL
2010-01-04   56.630001   57.869999   56.560001   41.200783    5277400  AMGN
2010-01-04   40.810001   41.099998   40.389999   33.090416    6894300   AXP
2010-01-04   55.720001   56.389999   54.799999   43.777565    6186700    BA
2010-01-04   57.650002   59.189999   57.509998   40.190220    7325600   CAT
...                ...         ...         ...         ...        ...   ...
2023-02-28  482.670013  483.359985  473.920013  465.066833    3902100   UNH
2023-02-28  220.000000  221.770004  219.500000  217.824539    5385400     V
2023-02-28   38.700001   38.970001   38.549999   35.538383   16685300    VZ
2023-02-28   35.480000   35.779999   35.320000   32.750980    8847000   WBA
2023-02-28   47.000000   47.549999   46.983334   46.346081   18054000   WMT

[97013 rows x 6 columns]

In [12]:
len(stock_data.tic.unique())

30

In [13]:
stock_data.tic.unique()

array(['AAPL', 'AMGN', 'AXP', 'BA', 'CAT', 'CRM', 'CSCO', 'CVX', 'DIS',
       'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'JPM', 'KO', 'MCD', 'MMM',
       'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'V', 'VZ', 'WBA', 'WMT',
       'DOW'], dtype=object)

In [14]:
stock_data_training

open        high         low       close     volume   tic
date                                                                       
2010-01-04    7.622500    7.660714    7.585000    6.461978  493729600  AAPL
2010-01-04   56.630001   57.869999   56.560001   41.200783    5277400  AMGN
2010-01-04   40.810001   41.099998   40.389999   33.090416    6894300   AXP
2010-01-04   55.720001   56.389999   54.799999   43.777565    6186700    BA
2010-01-04   57.650002   59.189999   57.509998   40.190220    7325600   CAT
...                ...         ...         ...         ...        ...   ...
2021-09-30  401.489990  403.489990  390.459991  375.759766    3779900   UNH
2021-09-30  227.580002  228.789993  222.630005  218.139236    7128500     V
2021-09-30   54.500000   54.509998   54.000000   45.622711   18736600    VZ
2021-09-30   48.790001   48.930000   46.919998   40.519119    6449400   WBA
2021-09-30   46.880001   47.243332   46.416668   44.566532   22457700   WMT

[86393 rows x 6 columns]

In [15]:
for ticker in tickers:
    # Filter the DataFrame for the ticker
    data = stock_data_training[stock_data_training['tic'] == ticker]
    
    # Drop the 'tic' column as mplfinance expects data with just OHLC and optionally volume
    ohlc_data = data[['open', 'high', 'low', 'close', 'volume']].copy()
    ohlc_data.index = pd.to_datetime(ohlc_data.index)  
    
    save_path = f'resultadosTFG/stockPrices/training/{ticker}_candlestick_chart.png'  
    mpf.plot(ohlc_data, type='candle', style='charles',
             title=f"{ticker} Candle",
             ylabel='Price ($)',
             volume=True,
             figsize=(10, 6),
             savefig=save_path)  

/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/mplfinance/_arg_validators.py:84: UserWarning: 


            POSSIBLE TO SEE DETAILS (Candles, Ohlc-Bars, Etc.)
   For more information see:
   - https://github.com/matplotlib/mplfinance/wiki/Plotting-Too-Much-Data
   
   TO SILENCE THIS WARNING, set `type='line'` in `mpf.plot()`
   OR set kwarg `warn_too_much_data=N` where N is an integer 
   LARGER than the number of data points you want to plot.

  warnings.warn('\n\n ================================================================= '+


/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/mplfinance/_arg_validators.py:84: UserWarning: 


            POSSIBLE TO SEE DETAILS (Candles, Ohlc-Bars, Etc.)
   For more information see:
   - https://github.com/matplotlib/mplfinance/wiki/Plotting-Too-Much-Data
   
   TO SILENCE THIS WARNING, set `type='line'` in `mpf.plot()`
   OR set kwarg `warn_too_much_data=N` where N is an integer 
   LARGER than the number of data points you want to plot.

  warnings.warn('\n\n ================================================================= '+
/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/mplfinance/_arg_validators.py:84: UserWarning: 


            POSSIBLE TO SEE DETAILS (Candles, Ohlc-Bars, Etc.)
   For more information see:
   - https://github.com/matplotlib/mplfinance/wiki/Plotting-Too-Much-Data
   
   TO SILENCE THIS WARNING, set `type='line'` in `mpf.plot()`
   OR set kwarg `warn_too_much_data=N` where N 

In [16]:
for ticker in tickers:
    # Filter the DataFrame for the ticker
    data = stock_data_testing[stock_data_testing['tic'] == ticker]
    
    # Drop the 'tic' column as mplfinance expects data with just OHLC and optionally volume
    ohlc_data = data[['open', 'high', 'low', 'close', 'volume']].copy()
    ohlc_data.index = pd.to_datetime(ohlc_data.index)  

    save_path = f'resultadosTFG/stockPrices/testing/{ticker}_candlestick_chart.png'  
    mpf.plot(ohlc_data, type='candle', style='charles',
             title=f"{ticker} Candle",
             ylabel='Price ($)',
             volume=True,
             figsize=(10, 6),
             savefig=save_path) 

In [14]:
for ticker in tickers:
    # Filter the DataFrame for the ticker
    data = stock_data_training[stock_data_training['tic'] == ticker]

    plt.figure(figsize=(10, 5))
    plt.plot(data.index, data['close'], label=f'Close Price of {ticker}')
    plt.title(f'Stock Closing Prices for Training {ticker}')
    plt.xlabel('Date')
    plt.ylabel('Close Price')
    plt.legend()
    plt.grid(True)

    
    plt.savefig(f'resultadosTFG/stockPrices/training/{ticker}_close_prices.png')

    plt.close()

In [17]:
for ticker in tickers:
    # Filter the DataFrame for the ticker
    data = stock_data_testing[stock_data_testing['tic'] == ticker]

    plt.figure(figsize=(10, 5))
    plt.plot(data.index, data['close'], label=f'Close Price of {ticker}')
    plt.title(f'Stock Closing Prices for Testing {ticker}')
    plt.xlabel('Date')
    plt.ylabel('Close Price')
    plt.legend()
    plt.grid(True)

    plt.savefig(f'resultadosTFG/stockPrices/testing/{ticker}_close_prices.png')

    plt.close()


In [18]:
plt.figure(figsize=(14, 7))

# Loop through each ticker and plot
for ticker in tickers:
    data = stock_data_training[stock_data_training['tic'] == ticker]
    plt.plot(data.index, data['close'], label=f'{ticker}')

plt.title('Stock Closing Prices for Training')
plt.xlabel('Date')
plt.ylabel('Close Price')
plt.legend(title='Ticker')
plt.grid(True)

plt.savefig(f'resultadosTFG/stockPrices/training/ALL_STOCKS_close_prices.png')

plt.close()

In [19]:
plt.figure(figsize=(14, 7))

# Loop through each ticker and plot
for ticker in tickers:
    data = stock_data_testing[stock_data_testing['tic'] == ticker]
    plt.plot(data.index, data['close'], label=f'{ticker}')

plt.title('Stock Closing Prices for Testing')
plt.xlabel('Date')
plt.ylabel('Close Price')
plt.legend(title='Ticker')
plt.grid(True)

plt.savefig(f'resultadosTFG/stockPrices/testing/ALL_STOCKS_close_prices.png')

plt.close()

## Agent 1

with following technical indicators:

In [16]:
# let's first take 4 technical indicators randomly from the supported indicators list
INDICATORS = [INDICATORS_LIST_ALL[i] for i in random.sample(range(len(INDICATORS_LIST_ALL)), 4)]

In [17]:
INDICATORS

['vr', 'trix', 'cr', 'vwma']

(Explain here why we need to use FeatureEngineer class)

In [18]:
# creamos instancia de FeatureEngineer indicando la configuración deseada para hacer el preproceso
fe = FeatureEngineer(
                    use_technical_indicator=True,
                    tech_indicator_list = INDICATORS,
                    use_vix=True, 
                    use_turbulence=True, # measures extreme asset price fluctuation --> if the turbulence index reaches a pre-defined threshold, the agent will halt buying action and start selling the holding shares gradually
                    user_defined_feature = False) 

processed = fe.preprocess_data(stock)

Successfully added technical indicators


[*********************100%%**********************]  1 of 1 completed


Shape of DataFrame:  (3310, 8)
Successfully added vix
Successfully added turbulence index


Comentario: hay indicadores que pese a estar documentados como soportados en https://pypi.org/project/stockstats/, esta versión de código no los reconoce. Habrá que comprobar mediante más pruebas que todos los incluídos en la lista de todos los indicadores, estén soportados por esta versión. 

In [19]:
processed

date        open        high         low       close     volume  \
0      2010-01-04    7.622500    7.660714    7.585000    6.461978  493729600   
1      2010-01-04   56.630001   57.869999   56.560001   41.200783    5277400   
2      2010-01-04   40.810001   41.099998   40.389999   33.090416    6894300   
3      2010-01-04   55.720001   56.389999   54.799999   43.777565    6186700   
4      2010-01-04   57.650002   59.189999   57.509998   40.190220    7325600   
...           ...         ...         ...         ...         ...        ...   
95985  2023-02-27  488.769989  490.940002  481.959991  472.278198    3006200   
95986  2023-02-27  220.729996  221.440002  219.339996  218.230591    4255300   
95987  2023-02-27   38.990002   39.150002   38.630001   35.602486   14210900   
95988  2023-02-27   36.049999   36.080002   35.270000   32.621933    5580100   
95989  2023-02-27   47.570000   47.696667   46.886665   46.121090   16647300   

        tic  day          vr      trix            cr        vwma        vix  \
0      AAPL    0  100.000000  0.000000           inf    7.235897  20.040001   
1      AMGN    0  100.000000  0.000000           inf   51.876928  20.040001   
2       AXP    0  100.000000  0.000000           inf   38.193471  20.040001   
3        BA    0  100.000000  0.000000           inf   51.655855  20.040001   
4       CAT    0  100.000000  0.000000           inf   52.296739  20.040001   
...     ...  ...         ...       ...           ...         ...        ...   
95985   UNH    0  102.479914 -0.024474  4.040793e+02  484.963830  20.950001   
95986     V    0   86.319011  0.006921  1.948805e+02  224.577449  20.950001   
95987    VZ    0  100.227548 -0.120141  1.387782e+04   38.651600  20.950001   
95988   WBA    0  136.358022 -0.024412  5.407458e+04   35.301067  20.950001   
95989   WMT    0  133.648352  0.041588  3.289840e+02   47.647771  20.950001   

       turbulence  
0        0.000000  
1        0.000000  
2        0.000000  
3        0.000000  
4        0.000000  
...           ...  
95985    7.163781  
95986    7.163781  
95987    7.163781  
95988    7.163781  
95989    7.163781  

[95990 rows x 14 columns]

In order to allow the Agent to have a consistent data structure to work with, we need to ensure that each stock has the same data range. This is necessary because not all stocks have data for every trading day due to holidays, stock-specific trading suspensions, or newly listed stocks. Therefore, we will establish a common data interval for each stock with day granularity and fill with 0 the (the more NaNs we have, the worst the performance will be). --> We can check this effect with other Stock Indices with less missing stock prices.

Convert the stock column to list

In [20]:
list_ticker = processed["tic"].unique().tolist()
print(list_ticker)
len(list_ticker)

['AAPL', 'AMGN', 'AXP', 'BA', 'CAT', 'CRM', 'CSCO', 'CVX', 'DIS', 'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'JPM', 'KO', 'MCD', 'MMM', 'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'V', 'VZ', 'WBA', 'WMT']


29

Create a list from the minimum to the maximum date and with the same granularity

In [21]:
list_date = list(pd.date_range(processed['date'].min(),processed['date'].max()).astype(str))
list_date

['2010-01-04',
 '2010-01-05',
 '2010-01-06',
 '2010-01-07',
 '2010-01-08',
 '2010-01-09',
 '2010-01-10',
 '2010-01-11',
 '2010-01-12',
 '2010-01-13',
 '2010-01-14',
 '2010-01-15',
 '2010-01-16',
 '2010-01-17',
 '2010-01-18',
 '2010-01-19',
 '2010-01-20',
 '2010-01-21',
 '2010-01-22',
 '2010-01-23',
 '2010-01-24',
 '2010-01-25',
 '2010-01-26',
 '2010-01-27',
 '2010-01-28',
 '2010-01-29',
 '2010-01-30',
 '2010-01-31',
 '2010-02-01',
 '2010-02-02',
 '2010-02-03',
 '2010-02-04',
 '2010-02-05',
 '2010-02-06',
 '2010-02-07',
 '2010-02-08',
 '2010-02-09',
 '2010-02-10',
 '2010-02-11',
 '2010-02-12',
 '2010-02-13',
 '2010-02-14',
 '2010-02-15',
 '2010-02-16',
 '2010-02-17',
 '2010-02-18',
 '2010-02-19',
 '2010-02-20',
 '2010-02-21',
 '2010-02-22',
 '2010-02-23',
 '2010-02-24',
 '2010-02-25',
 '2010-02-26',
 '2010-02-27',
 '2010-02-28',
 '2010-03-01',
 '2010-03-02',
 '2010-03-03',
 '2010-03-04',
 '2010-03-05',
 '2010-03-06',
 '2010-03-07',
 '2010-03-08',
 '2010-03-09',
 '2010-03-10',
 '2010-03-

Assign every day to each stock

In [22]:
combination = list(itertools.product(list_date,list_ticker))
combination

[('2010-01-04', 'AAPL'),
 ('2010-01-04', 'AMGN'),
 ('2010-01-04', 'AXP'),
 ('2010-01-04', 'BA'),
 ('2010-01-04', 'CAT'),
 ('2010-01-04', 'CRM'),
 ('2010-01-04', 'CSCO'),
 ('2010-01-04', 'CVX'),
 ('2010-01-04', 'DIS'),
 ('2010-01-04', 'GS'),
 ('2010-01-04', 'HD'),
 ('2010-01-04', 'HON'),
 ('2010-01-04', 'IBM'),
 ('2010-01-04', 'INTC'),
 ('2010-01-04', 'JNJ'),
 ('2010-01-04', 'JPM'),
 ('2010-01-04', 'KO'),
 ('2010-01-04', 'MCD'),
 ('2010-01-04', 'MMM'),
 ('2010-01-04', 'MRK'),
 ('2010-01-04', 'MSFT'),
 ('2010-01-04', 'NKE'),
 ('2010-01-04', 'PG'),
 ('2010-01-04', 'TRV'),
 ('2010-01-04', 'UNH'),
 ('2010-01-04', 'V'),
 ('2010-01-04', 'VZ'),
 ('2010-01-04', 'WBA'),
 ('2010-01-04', 'WMT'),
 ('2010-01-05', 'AAPL'),
 ('2010-01-05', 'AMGN'),
 ('2010-01-05', 'AXP'),
 ('2010-01-05', 'BA'),
 ('2010-01-05', 'CAT'),
 ('2010-01-05', 'CRM'),
 ('2010-01-05', 'CSCO'),
 ('2010-01-05', 'CVX'),
 ('2010-01-05', 'DIS'),
 ('2010-01-05', 'GS'),
 ('2010-01-05', 'HD'),
 ('2010-01-05', 'HON'),
 ('2010-01-05', 'IB

Merge with stock DF (potentially resulting in NaN values)

In [23]:
processed_full = pd.DataFrame(combination,columns=["date","tic"]).merge(processed,on=["date","tic"],how="left")

Remove non-trading days generated with the date range

In [24]:
processed_full = processed_full[processed_full['date'].isin(processed['date'])]

In [25]:
processed_full

date   tic        open        high         low       close  \
0       2010-01-04  AAPL    7.622500    7.660714    7.585000    6.461978   
1       2010-01-04  AMGN   56.630001   57.869999   56.560001   41.200783   
2       2010-01-04   AXP   40.810001   41.099998   40.389999   33.090416   
3       2010-01-04    BA   55.720001   56.389999   54.799999   43.777565   
4       2010-01-04   CAT   57.650002   59.189999   57.509998   40.190220   
...            ...   ...         ...         ...         ...         ...   
139282  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278198   
139283  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
139284  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602486   
139285  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621933   
139286  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121090   

             volume  day          vr      trix            cr        vwma  \
0       493729600.0  0.0  100.000000  0.000000           inf    7.235897   
1         5277400.0  0.0  100.000000  0.000000           inf   51.876928   
2         6894300.0  0.0  100.000000  0.000000           inf   38.193471   
3         6186700.0  0.0  100.000000  0.000000           inf   51.655855   
4         7325600.0  0.0  100.000000  0.000000           inf   52.296739   
...             ...  ...         ...       ...           ...         ...   
139282    3006200.0  0.0  102.479914 -0.024474  4.040793e+02  484.963830   
139283    4255300.0  0.0   86.319011  0.006921  1.948805e+02  224.577449   
139284   14210900.0  0.0  100.227548 -0.120141  1.387782e+04   38.651600   
139285    5580100.0  0.0  136.358022 -0.024412  5.407458e+04   35.301067   
139286   16647300.0  0.0  133.648352  0.041588  3.289840e+02   47.647771   

              vix  turbulence  
0       20.040001    0.000000  
1       20.040001    0.000000  
2       20.040001    0.000000  
3       20.040001    0.000000  
4       20.040001    0.000000  
...           ...         ...  
139282  20.950001    7.163781  
139283  20.950001    7.163781  
139284  20.950001    7.163781  
139285  20.950001    7.163781  
139286  20.950001    7.163781  

[95990 rows x 14 columns]

In [26]:
len(processed_full.tic.unique())

29

In [27]:
processed_full.info()

<class 'pandas.core.frame.DataFrame'>
Index: 95990 entries, 0 to 139286
Data columns (total 14 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   date        95990 non-null  object 
 1   tic         95990 non-null  object 
 2   open        95990 non-null  float64
 3   high        95990 non-null  float64
 4   low         95990 non-null  float64
 5   close       95990 non-null  float64
 6   volume      95990 non-null  float64
 7   day         95990 non-null  float64
 8   vr          95990 non-null  float64
 9   trix        95990 non-null  float64
 10  cr          95990 non-null  float64
 11  vwma        95990 non-null  float64
 12  vix         95990 non-null  float64
 13  turbulence  95990 non-null  float64
dtypes: float64(12), object(2)
memory usage: 11.0+ MB


In [28]:
processed_full.describe()

/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/pandas/core/nanops.py:1016: RuntimeWarning: invalid value encountered in subtract
  sqr = _ensure_numeric((avg - values) ** 2)
/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/numpy/lib/function_base.py:4655: RuntimeWarning: invalid value encountered in subtract
  diff_b_a = subtract(b, a)


open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.231167  1.995383e+07   
std       73.520545     74.279832     72.738958     70.603170  6.204278e+07   
min        6.870357      7.000000      6.794643      5.798899  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.924265  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.653954  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.492676  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day            vr          trix            cr          vwma  \
count  95990.000000  95990.000000  95990.000000  9.599000e+04  95990.000000   
mean       2.024471    118.221669      0.048224           inf     97.225648   
std        1.398649     54.812061      0.254111           NaN     72.055036   
min        0.000000      7.594460     -3.469403  1.685431e+01      6.663506   
25%        1.000000     80.435464     -0.086614  4.570783e+03     44.371047   
50%        2.000000    107.136477      0.061912           NaN     77.913010   
75%        3.000000    143.595369      0.199097           NaN    132.182716   
max        4.000000   1313.798187      1.917139           inf    540.258711   

                vix    turbulence  
count  95990.000000  95990.000000  
mean      18.721163     34.943609  
std        7.269653     43.066011  
min        9.140000      0.000000  
25%       13.630000     14.972803  
50%       16.875000     24.175536  
75%       21.760000     40.000148  
max       82.690002    652.620486

In this case, there are no nulls, but if there were we would need to fill them in the following way. 

In [29]:
processed_full = processed_full.sort_values(['date','tic']) # we need to sort bc of the data_split method CHECK SOURCE CODE 

processed_full = processed_full.fillna(0)

In [30]:
processed_full.describe()

/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/pandas/core/nanops.py:1016: RuntimeWarning: invalid value encountered in subtract
  sqr = _ensure_numeric((avg - values) ** 2)
/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/numpy/lib/function_base.py:4655: RuntimeWarning: invalid value encountered in subtract
  diff_b_a = subtract(b, a)


open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.231167  1.995383e+07   
std       73.520545     74.279832     72.738958     70.603170  6.204278e+07   
min        6.870357      7.000000      6.794643      5.798899  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.924265  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.653954  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.492676  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day            vr          trix            cr          vwma  \
count  95990.000000  95990.000000  95990.000000  9.599000e+04  95990.000000   
mean       2.024471    118.221669      0.048224           inf     97.225648   
std        1.398649     54.812061      0.254111           NaN     72.055036   
min        0.000000      7.594460     -3.469403  1.685431e+01      6.663506   
25%        1.000000     80.435464     -0.086614  4.570783e+03     44.371047   
50%        2.000000    107.136477      0.061912           NaN     77.913010   
75%        3.000000    143.595369      0.199097           NaN    132.182716   
max        4.000000   1313.798187      1.917139           inf    540.258711   

                vix    turbulence  
count  95990.000000  95990.000000  
mean      18.721163     34.943609  
std        7.269653     43.066011  
min        9.140000      0.000000  
25%       13.630000     14.972803  
50%       16.875000     24.175536  
75%       21.760000     40.000148  
max       82.690002    652.620486

In case there were infinite values in an indicator, to avoid numerical instability in the neural network, we will replace them with a large number instead (but there aren't in this case)

In [31]:
large_value = 1e9

processed_full.replace([np.inf], large_value, inplace=True)

In [32]:
processed_full

date   tic        open        high         low       close  \
0       2010-01-04  AAPL    7.622500    7.660714    7.585000    6.461978   
1       2010-01-04  AMGN   56.630001   57.869999   56.560001   41.200783   
2       2010-01-04   AXP   40.810001   41.099998   40.389999   33.090416   
3       2010-01-04    BA   55.720001   56.389999   54.799999   43.777565   
4       2010-01-04   CAT   57.650002   59.189999   57.509998   40.190220   
...            ...   ...         ...         ...         ...         ...   
139282  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278198   
139283  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
139284  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602486   
139285  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621933   
139286  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121090   

             volume  day          vr      trix            cr        vwma  \
0       493729600.0  0.0  100.000000  0.000000  1.000000e+09    7.235897   
1         5277400.0  0.0  100.000000  0.000000  1.000000e+09   51.876928   
2         6894300.0  0.0  100.000000  0.000000  1.000000e+09   38.193471   
3         6186700.0  0.0  100.000000  0.000000  1.000000e+09   51.655855   
4         7325600.0  0.0  100.000000  0.000000  1.000000e+09   52.296739   
...             ...  ...         ...       ...           ...         ...   
139282    3006200.0  0.0  102.479914 -0.024474  4.040793e+02  484.963830   
139283    4255300.0  0.0   86.319011  0.006921  1.948805e+02  224.577449   
139284   14210900.0  0.0  100.227548 -0.120141  1.387782e+04   38.651600   
139285    5580100.0  0.0  136.358022 -0.024412  5.407458e+04   35.301067   
139286   16647300.0  0.0  133.648352  0.041588  3.289840e+02   47.647771   

              vix  turbulence  
0       20.040001    0.000000  
1       20.040001    0.000000  
2       20.040001    0.000000  
3       20.040001    0.000000  
4       20.040001    0.000000  
...           ...         ...  
139282  20.950001    7.163781  
139283  20.950001    7.163781  
139284  20.950001    7.163781  
139285  20.950001    7.163781  
139286  20.950001    7.163781  

[95990 rows x 14 columns]

In [33]:
processed_full.describe()

open          high           low         close        volume  \
count  95990.000000  95990.000000  95990.000000  95990.000000  9.599000e+04   
mean     102.224117    103.175365    101.253646     88.231167  1.995383e+07   
std       73.520545     74.279832     72.738958     70.603170  6.204278e+07   
min        6.870357      7.000000      6.794643      5.798899  3.054000e+05   
25%       47.470001     47.910000     47.020000     38.924265  4.003909e+06   
50%       83.498051     84.139999     82.830002     67.653954  7.250700e+06   
75%      138.477531    139.731735    137.169998    118.492676  1.498672e+07   
max      555.000000    558.099976    550.130005    540.800171  1.880998e+09   

                day            vr          trix            cr          vwma  \
count  95990.000000  95990.000000  95990.000000  9.599000e+04  95990.000000   
mean       2.024471    118.221669      0.048224  6.309273e+08     97.225648   
std        1.398649     54.812061      0.254111  4.825486e+08     72.055036   
min        0.000000      7.594460     -3.469403  1.685431e+01      6.663506   
25%        1.000000     80.435464     -0.086614  4.570783e+03     44.371047   
50%        2.000000    107.136477      0.061912  1.000000e+09     77.913010   
75%        3.000000    143.595369      0.199097  1.000000e+09    132.182716   
max        4.000000   1313.798187      1.917139  1.000000e+09    540.258711   

                vix    turbulence  
count  95990.000000  95990.000000  
mean      18.721163     34.943609  
std        7.269653     43.066011  
min        9.140000      0.000000  
25%       13.630000     14.972803  
50%       16.875000     24.175536  
75%       21.760000     40.000148  
max       82.690002    652.620486

Split Train and Test datasets

In [34]:
train = data_split(processed_full, TRAIN_START_DATE,TRAIN_END_DATE)
train

date   tic        open        high         low       close  \
0     2010-01-04  AAPL    7.622500    7.660714    7.585000    6.461978   
0     2010-01-04  AMGN   56.630001   57.869999   56.560001   41.200783   
0     2010-01-04   AXP   40.810001   41.099998   40.389999   33.090416   
0     2010-01-04    BA   55.720001   56.389999   54.799999   43.777565   
0     2010-01-04   CAT   57.650002   59.189999   57.509998   40.190220   
...          ...   ...         ...         ...         ...         ...   
2956  2021-09-30   UNH  401.489990  403.489990  390.459991  375.759766   
2956  2021-09-30     V  227.580002  228.789993  222.630005  218.139236   
2956  2021-09-30    VZ   54.500000   54.509998   54.000000   45.622711   
2956  2021-09-30   WBA   48.790001   48.930000   46.919998   40.519119   
2956  2021-09-30   WMT   46.880001   47.243332   46.416668   44.566532   

           volume  day          vr      trix            cr        vwma  \
0     493729600.0  0.0  100.000000  0.000000  1.000000e+09    7.235897   
0       5277400.0  0.0  100.000000  0.000000  1.000000e+09   51.876928   
0       6894300.0  0.0  100.000000  0.000000  1.000000e+09   38.193471   
0       6186700.0  0.0  100.000000  0.000000  1.000000e+09   51.655855   
0       7325600.0  0.0  100.000000  0.000000  1.000000e+09   52.296739   
...           ...  ...         ...       ...           ...         ...   
2956    3779900.0  3.0   38.907914 -0.124240  8.206002e+02  404.511282   
2956    7128500.0  3.0   79.779065 -0.112169  2.558881e+02  222.888800   
2956   18736600.0  3.0   67.207132 -0.074152  1.000000e+09   51.552100   
2956    6449400.0  3.0   62.571527 -0.066341  1.000000e+09   46.584014   
2956   22457700.0  3.0   54.913154 -0.171315  3.205328e+03   47.146577   

            vix  turbulence  
0     20.040001    0.000000  
0     20.040001    0.000000  
0     20.040001    0.000000  
0     20.040001    0.000000  
0     20.040001    0.000000  
...         ...         ...  
2956  23.139999   24.927641  
2956  23.139999   24.927641  
2956  23.139999   24.927641  
2956  23.139999   24.927641  
2956  23.139999   24.927641  

[85753 rows x 14 columns]

In [35]:
len(train.tic.unique())

29

In [36]:
train.tic.unique()

array(['AAPL', 'AMGN', 'AXP', 'BA', 'CAT', 'CRM', 'CSCO', 'CVX', 'DIS',
       'GS', 'HD', 'HON', 'IBM', 'INTC', 'JNJ', 'JPM', 'KO', 'MCD', 'MMM',
       'MRK', 'MSFT', 'NKE', 'PG', 'TRV', 'UNH', 'V', 'VZ', 'WBA', 'WMT'],
      dtype=object)

In [37]:
trade = data_split(processed_full, TEST_START_DATE,TEST_END_DATE)
trade

date   tic        open        high         low       close  \
0    2021-10-01  AAPL  141.899994  142.919998  139.110001  140.462982   
0    2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822220   
0    2021-10-01   AXP  168.500000  175.119995  168.479996  167.727463   
0    2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0    2021-10-01   CAT  192.899994  195.869995  191.240005  183.513992   
..          ...   ...         ...         ...         ...         ...   
352  2023-02-27   UNH  488.769989  490.940002  481.959991  472.278198   
352  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
352  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602486   
352  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621933   
352  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121090   

         volume  day          vr      trix            cr        vwma  \
0    94639600.0  4.0   95.788460 -0.187907  1.736174e+02  144.317090   
0     2629400.0  4.0   84.197924 -0.224565  1.224122e+06  209.435411   
0     3956000.0  4.0  118.381291  0.218345  6.014149e+02  165.426148   
0     9113600.0  4.0  100.520123  0.012743  1.134938e+02  218.297611   
0     3695500.0  4.0   51.132369 -0.304558  8.853389e+02  192.977393   
..          ...  ...         ...       ...           ...         ...   
352   3006200.0  0.0  102.479914 -0.024474  4.040793e+02  484.963830   
352   4255300.0  0.0   86.319011  0.006921  1.948805e+02  224.577449   
352  14210900.0  0.0  100.227548 -0.120141  1.387782e+04   38.651600   
352   5580100.0  0.0  136.358022 -0.024412  5.407458e+04   35.301067   
352  16647300.0  0.0  133.648352  0.041588  3.289840e+02   47.647771   

           vix  turbulence  
0    21.100000  120.029860  
0    21.100000  120.029860  
0    21.100000  120.029860  
0    21.100000  120.029860  
0    21.100000  120.029860  
..         ...         ...  
352  20.950001    7.163781  
352  20.950001    7.163781  
352  20.950001    7.163781  
352  20.950001    7.163781  
352  20.950001    7.163781  

[10237 rows x 14 columns]

In [38]:
train_length = len(train)
trade_length = len(trade)
print("Number of training samples: ", train_length)
print("Number of testing samples", trade_length)

Number of training samples:  85753
Number of testing samples 10237


In [39]:
train.tail()

date  tic        open        high         low       close  \
2956  2021-09-30  UNH  401.489990  403.489990  390.459991  375.759766   
2956  2021-09-30    V  227.580002  228.789993  222.630005  218.139236   
2956  2021-09-30   VZ   54.500000   54.509998   54.000000   45.622711   
2956  2021-09-30  WBA   48.790001   48.930000   46.919998   40.519119   
2956  2021-09-30  WMT   46.880001   47.243332   46.416668   44.566532   

          volume  day         vr      trix            cr        vwma  \
2956   3779900.0  3.0  38.907914 -0.124240  8.206002e+02  404.511282   
2956   7128500.0  3.0  79.779065 -0.112169  2.558881e+02  222.888800   
2956  18736600.0  3.0  67.207132 -0.074152  1.000000e+09   51.552100   
2956   6449400.0  3.0  62.571527 -0.066341  1.000000e+09   46.584014   
2956  22457700.0  3.0  54.913154 -0.171315  3.205328e+03   47.146577   

            vix  turbulence  
2956  23.139999   24.927641  
2956  23.139999   24.927641  
2956  23.139999   24.927641  
2956  23.139999   24.927641  
2956  23.139999   24.927641

In [40]:
trade.head()

date   tic        open        high         low       close  \
0  2021-10-01  AAPL  141.899994  142.919998  139.110001  140.462982   
0  2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822220   
0  2021-10-01   AXP  168.500000  175.119995  168.479996  167.727463   
0  2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0  2021-10-01   CAT  192.899994  195.869995  191.240005  183.513992   

       volume  day          vr      trix            cr        vwma   vix  \
0  94639600.0  4.0   95.788460 -0.187907  1.736174e+02  144.317090  21.1   
0   2629400.0  4.0   84.197924 -0.224565  1.224122e+06  209.435411  21.1   
0   3956000.0  4.0  118.381291  0.218345  6.014149e+02  165.426148  21.1   
0   9113600.0  4.0  100.520123  0.012743  1.134938e+02  218.297611  21.1   
0   3695500.0  4.0   51.132369 -0.304558  8.853389e+02  192.977393  21.1   

   turbulence  
0   120.02986  
0   120.02986  
0   120.02986  
0   120.02986  
0   120.02986

Since we need to set the parameters for the environment functions, we need to compute the stock dimension and state space.

In [41]:
# Number of unique stocks used for the training 
stock_dimension = len(train.tic.unique())
# {balance, close price, shares, N-technical indicators}
# Balance will occupy 1 input node, and it is computed as: balance = balance (t) − amount of money we pay to buy shares + amount of money we receive to sell shares
# We will have N input nodes for the stock prices and N additional input nodes to indicate the current number of shares for each stock --> 2*N
# we will have one node for every technical indicator for every stock --> M indicators * N stocks
state_space = 1 + 2*stock_dimension + len(INDICATORS)*stock_dimension
print(f"Stock Dimension (Number of different companies in which we want to invest initially): {stock_dimension}, State Space (Number of input nodes to feed to the network): {state_space}")

Stock Dimension (Number of different companies in which we want to invest initially): 29, State Space (Number of input nodes to feed to the network): 175


Most of the trading companies demand trading commissions or costs. Here, we will simulate a buying and selling commission of 0,1% for each transaction. We will assume the user starts having no shares of any stock. Let's also assume we have 1.000.000 dollars to invest with. We will also define a parameter that sets the maximum amount of shares to trade, h_max. It is interesting to set the scaling reward or gamma (importance we give to the future reward), so that we specify if we give more importance to the short or long term. We could modify these parameters, if needed.

In [42]:
buy_cost_list = sell_cost_list = [0.001] * stock_dimension
num_stock_shares = [0] * stock_dimension
h_max = 100
initial_amount = 1000000
gamma = 1e-4 # we are assuming we want to get the highest return in the short term, preventing ourselves from the risk and uncertainty caused by external factors in the long term

(opcionalmente, podemos hacer pruebas con diferentes gammas y fechas)

Let's set the configuration that will be passed to the Environment class

In [43]:
env_kwargs = {
    "hmax": h_max,
    "initial_amount": initial_amount, 
    "num_stock_shares": num_stock_shares,
    "buy_cost_pct": buy_cost_list,
    "sell_cost_pct": sell_cost_list,
    "state_space": state_space,
    "stock_dim": stock_dimension,
    "tech_indicator_list": INDICATORS,
    "action_space": stock_dimension,
    "reward_scaling": gamma
}

Let's create the Stock Trading Environment

In [44]:
e_train_gym = StockTradingEnv(df = train, **env_kwargs) # creates instance of the Environment class
print("Environment class type", type(e_train_gym))
env_train, _ = e_train_gym.get_sb_env() # resets the environment and converts the initial environment into a DummyVecEnv instance
print("External Environment class type: ", type(env_train))

Environment class type <class 'finrl.meta.env_stock_trading.env_stocktrading.StockTradingEnv'>
External Environment class type:  <class 'stable_baselines3.common.vec_env.dummy_vec_env.DummyVecEnv'>


Since we will use different RL algorithms, let's set some flags:

In [45]:
if_using_a2c = True
if_using_ddpg = True
if_using_ppo = True
if_using_td3 = True
if_using_sac = True

Let's create the Deep Reinforcement Learning Agent!

# A2C

In [345]:
agent = DRLAgent(env = env_train) # creates Agent instance
model_a2c = agent.get_model("a2c") # gets stablebaselines3 model  

if if_using_a2c: # where to store the results
  # set up logger
  tmp_path = 'resultadosTFG' + '/a2c'
  new_logger_a2c = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_a2c.set_logger(new_logger_a2c)

{'n_steps': 5, 'ent_coef': 0.01, 'learning_rate': 0.0007}
Using cpu device
Logging to resultadosTFG/a2c


Let's train the agent

In [346]:
trained_a2c = agent.train_model(model=model_a2c, 
                             tb_log_name='a2c',
                             total_timesteps=50000) if if_using_a2c else None

--------------------------------------
| time/                 |            |
|    fps                | 162        |
|    iterations         | 100        |
|    time_elapsed       | 3          |
|    total_timesteps    | 500        |
| train/                |            |
|    entropy_loss       | -41.2      |
|    explained_variance | 0          |
|    learning_rate      | 0.0007     |
|    n_updates          | 99         |
|    policy_loss        | -48.3      |
|    reward             | 0.19467343 |
|    std                | 1          |
|    value_loss         | 1.95       |
--------------------------------------
-------------------------------------
| time/                 |           |
|    fps                | 167       |
|    iterations         | 200       |
|    time_elapsed       | 5         |
|    total_timesteps    | 1000      |
| train/                |           |
|    entropy_loss       | -41.2     |
|    explained_variance | -0.28     |
|    learning_rate      | 0.0007  

In [349]:
trained_a2c.policy

ActorCriticPolicy(
  (features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (pi_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (vf_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (mlp_extractor): MlpExtractor(
    (policy_net): Sequential(
      (0): Linear(in_features=175, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
    (value_net): Sequential(
      (0): Linear(in_features=175, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
  )
  (action_net): Linear(in_features=64, out_features=29, bias=True)
  (value_net): Linear(in_features=64, out_features=1, bias=True)
)

Let's see the learning progress of the agent

In [347]:
learning_process = pd.read_csv("resultadosTFG/a2c/progress.csv")
learning_process

train/reward  train/learning_rate  train/policy_loss  train/std  \
0       0.194673               0.0007         -48.275154   1.000829   
1       1.061061               0.0007         -38.645985   1.000853   
2      -2.992974               0.0007         -44.645302   0.999644   
3       1.349883               0.0007        -242.614700   1.000081   
4      -1.943858               0.0007        -295.775208   0.999879   
..           ...                  ...                ...        ...   
95     -1.765261               0.0007          33.249268   1.062274   
96     -0.639444               0.0007          56.227856   1.060504   
97      0.462060               0.0007        -231.903152   1.062978   
98     -1.323954               0.0007        -170.199203   1.062891   
99    -17.413000               0.0007         231.687988   1.059852   

    train/n_updates  time/total_timesteps  train/value_loss  time/fps  \
0                99                   500          1.949795       162   
1               199                  1000          6.455199       167   
2               299                  1500          7.954846       172   
3               399                  2000         39.553139       177   
4               499                  2500         71.763481       180   
..              ...                   ...               ...       ...   
95             9599                 48000          2.292641       187   
96             9699                 48500          2.496875       187   
97             9799                 49000         32.458706       186   
98             9899                 49500         16.457235       186   
99             9999                 50000         37.186180       186   

    time/iterations  train/explained_variance  time/time_elapsed  \
0               100              0.000000e+00                  3   
1               200             -2.800968e-01                  5   
2               300              0.000000e+00                  8   
3               400              0.000000e+00                 11   
4               500              0.000000e+00                 13   
..              ...                       ...                ...   
95             9600              0.000000e+00                255   
96             9700              0.000000e+00                258   
97             9800              0.000000e+00                262   
98             9900             -1.192093e-07                264   
99            10000              0.000000e+00                267   

    train/entropy_loss  
0           -41.168213  
1           -41.157383  
2           -41.138073  
3           -41.146381  
4           -41.134689  
..                 ...  
95          -42.853855  
96          -42.806717  
97          -42.868977  
98          -42.872429  
99          -42.788807  

[100 rows x 12 columns]

Plot the training results

In [348]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten() 

    metrics = [
        ('train/reward', 'Reward'),
        ('train/policy_loss', 'Policy Loss'),
        ('train/std', 'Standard Deviation'),
        ('train/n_updates', 'Number of Updates'),
        ('train/value_loss', 'Value Loss'),
        ('time/fps', 'Frames Per Second'),
        ('train/explained_variance', 'Explained Variance'),
        ('train/entropy_loss', 'Entropy Loss')
    ]

    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/a2c/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=2)  # Modify n_rows and n_cols as needed


# PPO

Set PPO parameters and set the logger

In [350]:
agent = DRLAgent(env = env_train)
PPO_PARAMS = {
    "n_steps": 2048,
    "ent_coef": 0.01,
    "learning_rate": 0.00025,
    "batch_size": 128,
}
model_ppo = agent.get_model("ppo",model_kwargs = PPO_PARAMS)

if if_using_ppo:
  # set up logger
  tmp_path = 'resultadosTFG' + '/ppo'
  new_logger_ppo = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_ppo.set_logger(new_logger_ppo)

{'n_steps': 2048, 'ent_coef': 0.01, 'learning_rate': 0.00025, 'batch_size': 128}
Using cpu device
Logging to resultadosTFG/ppo


Train PPO

In [351]:
trained_ppo = agent.train_model(model=model_ppo, 
                             tb_log_name='ppo',
                             total_timesteps=50000) if if_using_ppo else None

----------------------------------
| time/              |           |
|    fps             | 209       |
|    iterations      | 1         |
|    time_elapsed    | 9         |
|    total_timesteps | 2048      |
| train/             |           |
|    reward          | 1.1433591 |
----------------------------------
-----------------------------------------
| time/                   |             |
|    fps                  | 206         |
|    iterations           | 2           |
|    time_elapsed         | 19          |
|    total_timesteps      | 4096        |
| train/                  |             |
|    approx_kl            | 0.013885733 |
|    clip_fraction        | 0.195       |
|    clip_range           | 0.2         |
|    entropy_loss         | -41.2       |
|    explained_variance   | -0.0255     |
|    learning_rate        | 0.00025     |
|    loss                 | 6.14        |
|    n_updates            | 10          |
|    policy_gradient_loss | -0.025      |
|    reward  

In [352]:
trained_ppo.policy

ActorCriticPolicy(
  (features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (pi_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (vf_features_extractor): FlattenExtractor(
    (flatten): Flatten(start_dim=1, end_dim=-1)
  )
  (mlp_extractor): MlpExtractor(
    (policy_net): Sequential(
      (0): Linear(in_features=175, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
    (value_net): Sequential(
      (0): Linear(in_features=175, out_features=64, bias=True)
      (1): Tanh()
      (2): Linear(in_features=64, out_features=64, bias=True)
      (3): Tanh()
    )
  )
  (action_net): Linear(in_features=64, out_features=29, bias=True)
  (value_net): Linear(in_features=64, out_features=1, bias=True)
)

Let's see the learning progress of the agent

In [354]:
learning_process = pd.read_csv("resultadosTFG/ppo/progress.csv")
learning_process

time/total_timesteps  time/fps  train/reward  time/iterations  \
0                   2048       209      1.143359                1   
1                   4096       206     -0.349447                2   
2                   6144       194      1.891322                3   
3                   8192       196      1.716068                4   
4                  10240       198     -1.300342                5   
5                  12288       199      0.119303                6   
6                  14336       200      2.794655                7   
7                  16384       201     -1.934596                8   
8                  18432       200      1.430494                9   
9                  20480       201      1.843483               10   
10                 22528       202     -0.888785               11   
11                 24576       202      0.505270               12   
12                 26624       203     -0.210483               13   
13                 28672       202      6.598871               14   
14                 30720       202      0.437785               15   
15                 32768       202      0.423983               16   
16                 34816       203     -4.204621               17   
17                 36864       202     -4.295562               18   
18                 38912       202     -0.862714               19   
19                 40960       202     -2.084643               20   
20                 43008       202     -0.378369               21   
21                 45056       202     -0.317228               22   
22                 47104       202     -0.063254               23   
23                 49152       203     -0.024401               24   
24                 51200       203      1.835830               25   

    time/time_elapsed  train/clip_fraction  train/loss  \
0                   9                  NaN         NaN   
1                  19             0.195215    6.135874   
2                  31             0.156982    8.931610   
3                  41             0.147168   32.045990   
4                  51             0.184277   12.381388   
5                  61             0.178760   38.620510   
6                  71             0.208447   23.979141   
7                  81             0.161670   14.617854   
8                  91             0.189844   36.720249   
9                 101             0.147754   18.057995   
10                111             0.245264   35.471447   
11                121             0.208350    9.632629   
12                131             0.242139   86.749901   
13                141             0.218994   12.200534   
14                151             0.276123   11.748824   
15                161             0.198779   43.691498   
16                171             0.102002  116.300232   
17                181             0.199365   11.269382   
18                191             0.208203   82.986176   
19                202             0.216895   41.079472   
20                212             0.251172    9.084751   
21                222             0.233252   13.714664   
22                232             0.146094   47.060349   
23                241             0.244238   28.126547   
24                251             0.276465   11.621744   

    train/explained_variance  train/learning_rate  train/std  \
0                        NaN                  NaN        NaN   
1                  -0.025466              0.00025   1.003091   
2                   0.000314              0.00025   1.004078   
3                  -0.010601              0.00025   1.007110   
4                  -0.021251              0.00025   1.009133   
5                  -0.002551              0.00025   1.012016   
6                  -0.005971              0.00025   1.012480   
7                   0.002221              0.00025   1.013131   
8                  -0.006657              0.00025   1.014888   
9                  -0.002122              0.00025   1.016218

Plot the training results

In [359]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  

    metrics = [
        ('train/reward', 'Reward'),
        ('train/loss', 'Loss'),
        ('train/std', 'Standard Deviation'),
        ('train/approx_kl', 'approximate Kullback-Leibler divergence'),
        ('train/clip_fraction', 'Clip Fraction'),
        ('train/clip_range', 'Clip Range'),
        ('train/explained_variance', 'Explained Variance'),
        ('train/value_loss', 'Value Loss'),
        ('train/policy_gradient_loss', 'Policy Gradient Loss'),
        ('train/entropy_loss', 'Entropy Loss')
    ]

    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/ppo/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=5, n_cols=2)  # Modify n_rows and n_cols as needed

# DDPG

Create the agent and set the logger

In [46]:
agent = DRLAgent(env = env_train)
model_ddpg = agent.get_model("ddpg")
model_ddpg.learning_rate = 0.00001
if if_using_ddpg:
  # set up logger
  tmp_path = 'resultadosTFG' + '/ddpg'
  new_logger_ddpg = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_ddpg.set_logger(new_logger_ddpg)

estoy usando este models
{'batch_size': 128, 'buffer_size': 50000, 'learning_rate': 1e-05}
Using cpu device
Logging to resultadosTFG/ddpg


Train the agent

In [47]:
trained_ddpg = agent.train_model(model=model_ddpg, 
                             tb_log_name='ddpg',
                             total_timesteps=50000) if if_using_ddpg else None

-----------------------------------
| time/              |            |
|    episodes        | 4          |
|    fps             | 121        |
|    time_elapsed    | 97         |
|    total_timesteps | 11828      |
| train/             |            |
|    actor_loss      | -2.08e+07  |
|    critic_loss     | 7.46e+11   |
|    learning_rate   | 1e-05      |
|    n_updates       | 8871       |
|    reward          | -8.4297905 |
-----------------------------------
-----------------------------------
| time/              |            |
|    episodes        | 8          |
|    fps             | 115        |
|    time_elapsed    | 205        |
|    total_timesteps | 23656      |
| train/             |            |
|    actor_loss      | -1.11e+07  |
|    critic_loss     | 1.55e+11   |
|    learning_rate   | 1e-05      |
|    n_updates       | 20699      |
|    reward          | -8.4297905 |
-----------------------------------
day: 2956, episode: 10
begin_total_asset: 1000000.00
end_total_a

In [48]:
trained_ddpg.policy

TD3Policy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=175, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (actor_target): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=175, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=204, out_

Let's see the learning progress of the agent 

In [49]:
learning_process = pd.read_csv("resultadosTFG/ddpg/progress.csv")
learning_process

train/critic_loss  train/learning_rate  time/time_elapsed  train/reward  \
0       7.460041e+11              0.00001                 97      -8.42979   
1       1.553868e+11              0.00001                205      -8.42979   
2       3.304225e+10              0.00001                326      -8.42979   
3       9.698949e+09              0.00001                430      -8.42979   

   train/n_updates  time/total_timesteps  time/episodes  time/fps  \
0             8871                 11828              4       121   
1            20699                 23656              8       115   
2            32527                 35484             12       108   
3            44355                 47312             16       109   

   train/actor_loss  
0     -2.075582e+07  
1     -1.108353e+07  
2     -5.980257e+06  
3     -3.268074e+06

Plot the results of the training

In [52]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/n_updates', 'Number of Updates'),
        ('train/critic_loss', 'Critic Loss')
    ]

    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/setnuevoprueba/ddpg/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=1)  # Modify n_rows and n_cols as needed

# TD3

Create the agent and set the logger

In [365]:
agent = DRLAgent(env = env_train)
TD3_PARAMS = {"batch_size": 100, 
              "buffer_size": 1000000, 
              "learning_rate": 0.001}

model_td3 = agent.get_model("td3",model_kwargs = TD3_PARAMS)

if if_using_td3:
  # set up logger
  tmp_path = 'resultadosTFG' + '/td3'
  new_logger_td3 = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_td3.set_logger(new_logger_td3)

{'batch_size': 100, 'buffer_size': 1000000, 'learning_rate': 0.001}
Using cpu device
Logging to resultadosTFG/td3


/Users/carolinaalbamaruganrubio/miniforge3/envs/ai4finance/lib/python3.10/site-packages/stable_baselines3/common/buffers.py:241: UserWarning: This system does not have apparently enough memory to store the complete replay buffer 1.52GB > 1.36GB
  warnings.warn(


Train TD3

In [366]:
trained_td3 = agent.train_model(model=model_td3, 
                             tb_log_name='td3',
                             total_timesteps=50000) if if_using_td3 else None

----------------------------------
| time/              |           |
|    episodes        | 4         |
|    fps             | 105       |
|    time_elapsed    | 111       |
|    total_timesteps | 11828     |
| train/             |           |
|    actor_loss      | 63.9      |
|    critic_loss     | 1.8e+03   |
|    learning_rate   | 0.001     |
|    n_updates       | 8871      |
|    reward          | -9.668041 |
----------------------------------
day: 2956, episode: 60
begin_total_asset: 1000000.00
end_total_asset: 5101279.40
total_reward: 4101279.40
total_cost: 999.00
total_trades: 26604
Sharpe: 0.823
----------------------------------
| time/              |           |
|    episodes        | 8         |
|    fps             | 104       |
|    time_elapsed    | 225       |
|    total_timesteps | 23656     |
| train/             |           |
|    actor_loss      | 4.64      |
|    critic_loss     | 579       |
|    learning_rate   | 0.001     |
|    n_updates       | 20699     |
|

In [367]:
trained_td3.policy

TD3Policy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=175, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (actor_target): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (mu): Sequential(
      (0): Linear(in_features=175, out_features=400, bias=True)
      (1): ReLU()
      (2): Linear(in_features=400, out_features=300, bias=True)
      (3): ReLU()
      (4): Linear(in_features=300, out_features=29, bias=True)
      (5): Tanh()
    )
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=204, out_

Let's see agent's learning process

In [368]:
learning_process = pd.read_csv("resultadosTFG/td3/progress.csv")
learning_process

train/actor_loss  train/reward  train/learning_rate  train/n_updates  \
0         63.926686     -9.668041                0.001             8871   
1          4.635762     -9.668041                0.001            20699   
2          3.998228     -9.668041                0.001            32527   
3         14.913754     -9.668041                0.001            44355   

   time/total_timesteps  time/fps  time/episodes  time/time_elapsed  \
0                 11828       105              4                111   
1                 23656       104              8                225   
2                 35484       102             12                347   
3                 47312       101             16                464   

   train/critic_loss  
0        1800.738227  
1         578.985548  
2          44.579082  
3          28.977232

Plot training results

In [370]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/n_updates', 'Number of Updates'),
        ('train/critic_loss', 'Critic Loss')
    ]

    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/td3/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=4, n_cols=1)  # Modify n_rows and n_cols as needed

# SAC

Create the agent, set parameters for training, and set logger

In [371]:
agent = DRLAgent(env = env_train)
SAC_PARAMS = {
    "batch_size": 128,
    "buffer_size": 100000,
    "learning_rate": 0.0001,
    "learning_starts": 100,
    "ent_coef": "auto_0.1",
}

model_sac = agent.get_model("sac",model_kwargs = SAC_PARAMS)

if if_using_sac:
  # set up logger
  tmp_path = 'resultadosTFG' + '/sac'
  new_logger_sac = configure(tmp_path, ["stdout", "csv", "tensorboard"])
  # Set new logger
  model_sac.set_logger(new_logger_sac)

{'batch_size': 128, 'buffer_size': 100000, 'learning_rate': 0.0001, 'learning_starts': 100, 'ent_coef': 'auto_0.1'}
Using cpu device
Logging to resultadosTFG/sac


Train SAC

In [372]:
trained_sac = agent.train_model(model=model_sac, 
                             tb_log_name='sac',
                             total_timesteps=50000) if if_using_sac else None

-----------------------------------
| time/              |            |
|    episodes        | 4          |
|    fps             | 79         |
|    time_elapsed    | 149        |
|    total_timesteps | 11828      |
| train/             |            |
|    actor_loss      | 726        |
|    critic_loss     | 54.8       |
|    ent_coef        | 0.149      |
|    ent_coef_loss   | -87        |
|    learning_rate   | 0.0001     |
|    n_updates       | 11727      |
|    reward          | -14.443684 |
-----------------------------------
day: 2956, episode: 80
begin_total_asset: 1000000.00
end_total_asset: 4086097.19
total_reward: 3086097.19
total_cost: 13960.36
total_trades: 50920
Sharpe: 0.722
----------------------------------
| time/              |           |
|    episodes        | 8         |
|    fps             | 77        |
|    time_elapsed    | 306       |
|    total_timesteps | 23656     |
| train/             |           |
|    actor_loss      | 266       |
|    critic_loss   

In [373]:
trained_sac.policy

SACPolicy(
  (actor): Actor(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (latent_pi): Sequential(
      (0): Linear(in_features=175, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=256, bias=True)
      (3): ReLU()
    )
    (mu): Linear(in_features=256, out_features=29, bias=True)
    (log_std): Linear(in_features=256, out_features=29, bias=True)
  )
  (critic): ContinuousCritic(
    (features_extractor): FlattenExtractor(
      (flatten): Flatten(start_dim=1, end_dim=-1)
    )
    (qf0): Sequential(
      (0): Linear(in_features=204, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=256, bias=True)
      (3): ReLU()
      (4): Linear(in_features=256, out_features=1, bias=True)
    )
    (qf1): Sequential(
      (0): Linear(in_features=204, out_features=256, bias=True)
      (1): ReLU()
      (2): Linear(in_features=256, out_features=2

Let's see agent's learning process

In [374]:
learning_process = pd.read_csv("resultadosTFG/sac/progress.csv")
learning_process

train/actor_loss  train/reward  train/learning_rate  train/n_updates  \
0        726.397827    -14.443684               0.0001            11727   
1        266.153259     -8.754704               0.0001            23555   
2        132.993698     -5.745950               0.0001            35383   
3         69.045204     -5.567561               0.0001            47211   

   train/ent_coef_loss  time/total_timesteps  time/fps  time/episodes  \
0           -86.965622                 11828        79              4   
1          -112.916206                 23656        77              8   
2          -114.863518                 35484        75             12   
3           -73.456841                 47312        75             16   

   train/ent_coef  time/time_elapsed  train/critic_loss  
0        0.149189                149          54.831455  
1        0.044710                306          76.029633  
2        0.014124                469          53.002083  
3        0.004607                628           8.636238

Agent's training results

In [377]:
def plot_metrics(df, n_rows, n_cols):
    fig, axes = plt.subplots(nrows=n_rows, ncols=n_cols, figsize=(5 * n_cols, 5 * n_rows))
    axes = axes.flatten()  

    metrics = [
        ('train/reward', 'Reward'),
        ('train/actor_loss', 'Actor Loss'),
        ('train/ent_coef_loss', 'Entropy coefficient Loss'),
        ('train/ent_coef', 'Entropy coefficient'),
        ('train/critic_loss', 'Critic Loss')
    ]

    for ax, (metric, title) in zip(axes, metrics):
        ax.plot(df['time/total_timesteps'], df[metric], label=title)
        ax.set_xlabel('Total Timesteps')
        ax.set_ylabel(title)
        ax.set_title(title)
        ax.grid(True)
        ax.legend()

    plt.tight_layout()
    plt.savefig(f'resultadosTFG/sac/trainingStatsResults.png')
    plt.close()

df = learning_process
plot_metrics(df, n_rows=5, n_cols=1)  # Modify n_rows and n_cols as needed

# Testing

There is a new environment for testing

We feed the environment with the testing dataset we prepared before (from start test date to end test date: with closing prices, etc)

In [379]:
e_trade_gym = StockTradingEnv(df = trade, turbulence_threshold = 70,risk_indicator_col='vix', **env_kwargs)
e_trade_gym

Environment from Stable baselines3; observations is a matrix containing the inputs {balance, close price, shares, N-technical indicators}

In [380]:
env_trade, obs_trade = e_trade_gym.get_sb_env()
env_trade

In [ ]:
obs_trade

In [382]:
trade

date   tic        open        high         low       close  \
0    2021-10-01  AAPL  141.899994  142.919998  139.110001  140.653519   
0    2021-10-01  AMGN  213.589996  214.610001  210.800003  195.822250   
0    2021-10-01   AXP  168.500000  175.119995  168.479996  167.727463   
0    2021-10-01    BA  222.850006  226.720001  220.600006  226.000000   
0    2021-10-01   CAT  192.899994  195.869995  191.240005  183.513992   
..          ...   ...         ...         ...         ...         ...   
352  2023-02-27   UNH  488.769989  490.940002  481.959991  474.281799   
352  2023-02-27     V  220.729996  221.440002  219.339996  218.230591   
352  2023-02-27    VZ   38.990002   39.150002   38.630001   35.602482   
352  2023-02-27   WBA   36.049999   36.080002   35.270000   32.621925   
352  2023-02-27   WMT   47.570000   47.696667   46.886665   46.121090   

         volume  day  high_5_sma        boll   stochrsi        adx        vix  \
0    94639600.0  4.0  144.492001  145.480990  36.066603  51.586046  21.100000   
0     2629400.0  4.0  215.557999  197.962445  75.148909  33.147887  21.100000   
0     3956000.0  4.0  175.300000  159.502596  65.456090  23.039918  21.100000   
0     9113600.0  4.0  227.198001  216.318501  95.477772  13.576357  21.100000   
0     3695500.0  4.0  199.956000  189.037466  66.701686  33.844287  21.100000   
..          ...  ...         ...         ...        ...        ...        ...   
352   3006200.0  0.0  494.414001  478.165260  32.661661  11.867177  20.950001   
352   4255300.0  0.0  221.592001  224.423514   7.819749  41.614291  20.950001   
352  14210900.0  0.0   39.360000   36.881720  26.473055  40.124667  20.950001   
352   5580100.0  0.0   36.282000   33.398429   2.330210  26.347004  20.950001   
352  16647300.0  0.0   48.407333   46.782871  15.558537  24.757027  20.950001   

     turbulence  
0    120.031177  
0    120.031177  
0    120.031177  
0    120.031177  
0    120.031177  
..          ...  
352    7.163893  
352    7.163893  
352    7.163893  
352    7.163893  
352    7.163893  

[10237 rows x 14 columns]

## A2C

Test, predict

Account value is the DF that stores the history of the value of the assets (portfolio value) when used that algorithm

In [383]:
trained_model = trained_a2c
df_account_value_a2c, df_actions_a2c = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[1.00000000e+06 1.40653519e+02 1.95822250e+02 1.67727463e+02
  2.26000000e+02 1.83513992e+02 2.74900909e+02 5.07116776e+01
  9.38071213e+01 1.75438217e+02 3.52330719e+02 3.07771027e+02
  2.03622513e+02 1.20424385e+02 5.01258202e+01 1.48433197e+02
  1.54524490e+02 4.87658386e+01 2.28277725e+02 1.26340271e+02
  7.55181961e+01 2.82348145e+02 1.42315796e+02 1.30338394e+02
  1.43675705e+02 3.78985962e+02 2.25689667e+02 4.58676834e+01
  4.03038177e+01 4.38215256e+01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 1.44492004e+02
  2.15557999e+02 1.75300003e+02 2

Plot and Save testing results, Portfolio Value

In [488]:
df_account_value_a2c['date'] = pd.to_datetime(df_account_value_a2c['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_a2c['date'], df_account_value_a2c['account_value'])

locator = mdates.MonthLocator(interval=1) 
plt.gca().xaxis.set_major_locator(locator)

formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for A2C')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/a2c/testing/accountValue.png')
plt.close()

Trades made in testing

In [388]:
display(df_actions_a2c)

AAPL  AMGN  AXP   BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  \
date                                                            ...        
2021-10-01    32     0    0  100   83   28     0   30    0   0  ...  100   
2021-10-04    32     0    0  100   83   28     0   30    0   0  ...  100   
2021-10-05    32     0    0  100   83   28     0   30    0   0  ...  100   
2021-10-06    32     0    0  100   83   28     0   30    0   0  ...  100   
2021-10-07    32     0    0  100   83   28     0   30    0   0  ...  100   
...          ...   ...  ...  ...  ...  ...   ...  ...  ...  ..  ...  ...   
2023-02-17     0     0    0    0    0    0     0    0    0   0  ...    0   
2023-02-21     0     0    0    0    0    0     0    0    0   0  ...    0   
2023-02-22     0     0    0    0    0    0     0    0    0   0  ...    0   
2023-02-23     0     0    0    0    0    0     0    0    0   0  ...    0   
2023-02-24     0     0    0    0    0    0     0    0    0   0  ...    0   

            MSFT  NKE  PG  TRV  UNH  V  VZ  WBA  WMT  
date                                                  
2021-10-01     0  100  70    8  100  0   0  100    0  
2021-10-04     0  100  70    8  100  0   0  100    0  
2021-10-05     0  100  70    8  100  0   0  100    0  
2021-10-06     0  100  70    8  100  0   0  100    0  
2021-10-07     0  100  70    8  100  0   0  100    0  
...          ...  ...  ..  ...  ... ..  ..  ...  ...  
2023-02-17     0    0   0    0    0  0   0    0    0  
2023-02-21     0    0   0    0    0  0   0    0    0  
2023-02-22     0    0   0    0    0  0   0    0    0  
2023-02-23     0    0   0    0    0  0   0    0    0  
2023-02-24     0    0   0    0    0  0   0    0    0  

[352 rows x 29 columns]

## PPO

Test, predict

In [453]:
trained_model = trained_ppo
df_account_value_ppo, df_actions_ppo = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[1.00000000e+06 1.40653519e+02 1.95822250e+02 1.67727463e+02
  2.26000000e+02 1.83513992e+02 2.74900909e+02 5.07116776e+01
  9.38071213e+01 1.75438217e+02 3.52330719e+02 3.07771027e+02
  2.03622513e+02 1.20424385e+02 5.01258202e+01 1.48433197e+02
  1.54524490e+02 4.87658386e+01 2.28277725e+02 1.26340271e+02
  7.55181961e+01 2.82348145e+02 1.42315796e+02 1.30338394e+02
  1.43675705e+02 3.78985962e+02 2.25689667e+02 4.58676834e+01
  4.03038177e+01 4.38215256e+01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 1.44492004e+02
  2.15557999e+02 1.75300003e+02 2

Save Plot of Portfolio Value

In [489]:
df_account_value_ppo['date'] = pd.to_datetime(df_account_value_ppo['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_ppo['date'], df_account_value_ppo['account_value'])

locator = mdates.MonthLocator(interval=1)  
plt.gca().xaxis.set_major_locator(locator)

formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for PPO')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/ppo/testing/accountValue.png')
plt.close()


Trades made in testing

In [458]:
df_actions_ppo.tail(40)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  MSFT  \
date                                                           ...              
2022-12-28     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2022-12-29     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2022-12-30     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-04     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-05     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-06     0     0    0   0    0    1     0    0    0   0  ...    0     0   
2023-01-09     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-11     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-12     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-13     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-17     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-18     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-19     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-20     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-23     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-24     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-25     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-26     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-27     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-30     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-01-31     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-01     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-02     0    -4    0   0    3    0     0    0    0   0  ...    0     0   
2023-02-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-06     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-07     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-08     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-09     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-13     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-14     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-15     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-16     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-17     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-21     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-22     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-23     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2023-02-24     0     0    0   0    0    0     0    0    0   0  ...    0     0   

            NKE  PG  TRV  UNH  V  VZ  WBA  WMT  
date                                            
2022-12-28    0   0    0    0  0   0    0    0  
2022-12-29    0   0    0    0  0   0    0    0  
2022-12-30    0   0    0    0  0   0    0    0  
2023-01-03    0   0    0    0  0   0    0    0  
2023-01-04    0   0    0    0  0   0    0    0  
2023-01-05    0   0    0    0  0   0    0    0  
2023-01-06   -1   0    0    0  0   0    0    0  
2023-01-09    0   0    0    0  0   0    0    0  
2023-01-10    0   0    0    0  0   0    0    0  
2023-01-11    0   0    0    0  0   0    0    0  
2023-01-12    0   0  

## DDPG

Test DDPG, predict

In [407]:
trained_model = trained_ddpg
df_account_value_ddpg, df_actions_ddpg = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[1.00000000e+06 1.40653519e+02 1.95822250e+02 1.67727463e+02
  2.26000000e+02 1.83513992e+02 2.74900909e+02 5.07116776e+01
  9.38071213e+01 1.75438217e+02 3.52330719e+02 3.07771027e+02
  2.03622513e+02 1.20424385e+02 5.01258202e+01 1.48433197e+02
  1.54524490e+02 4.87658386e+01 2.28277725e+02 1.26340271e+02
  7.55181961e+01 2.82348145e+02 1.42315796e+02 1.30338394e+02
  1.43675705e+02 3.78985962e+02 2.25689667e+02 4.58676834e+01
  4.03038177e+01 4.38215256e+01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 1.44492004e+02
  2.15557999e+02 1.75300003e+02 2

Store graph of the value of portfolio

In [491]:
df_account_value_ddpg['date'] = pd.to_datetime(df_account_value_ddpg['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_ddpg['date'], df_account_value_ddpg['account_value'])

locator = mdates.MonthLocator(interval=1) 
plt.gca().xaxis.set_major_locator(locator)

formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for DDPG')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/ddpg/testing/accountValue.png')
plt.close()


Trades made in testing

In [410]:
df_actions_ddpg.head(30)

AAPL  AMGN  AXP   BA  CAT  CRM  CSCO  CVX  DIS   GS  ...  MRK  \
date                                                             ...        
2021-10-01     0     0  100  100    0    0   100  100    0  100  ...    0   
2021-10-04     0     0  100  100    0    0   100  100    0  100  ...    0   
2021-10-05     0     0  100  100    0    0   100  100    0  100  ...    0   
2021-10-06     0     0  100  100    0    0   100  100    0  100  ...    0   
2021-10-07     0     0  100  100    0    0   100  100    0  100  ...    0   
2021-10-08     0     0  100  100    0    0   100  100    0    0  ...    0   
2021-10-11     0     0    0    0    0    0     1 -100    0    0  ...    0   
2021-10-12     0     0    0    0    0    0     0 -100    0    0  ...    0   
2021-10-13     0     0    0    0    0    0     2 -100    0    0  ...    0   
2021-10-14     0     0    0    0    0    0     0 -100    0    0  ...    0   
2021-10-15     0     0    0    0    0    0     0 -100    0    0  ...    0   
2021-10-18     0     0    0    0    0    0     1 -100    0    0  ...    0   
2021-10-19     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-20     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-21     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-22     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-25     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-26     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-27     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-28     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-10-29     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-01     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-02     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-03     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-04     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-05     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-08     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-09     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-10     0     0    0    0    0    0     0    0    0    0  ...    0   
2021-11-11     0     0    0    0    0    0     0    0    0    0  ...    0   

            MSFT  NKE   PG  TRV  UNH    V   VZ  WBA  WMT  
date                                                      
2021-10-01     0  100  100  100    0  100  100    0  100  
2021-10-04     0  100  100  100    0  100  100    0  100  
2021-10-05     0  100  100  100    0  100  100    0  100  
2021-10-06     0  100  100  100    0  100  100    0  100  
2021-10-07     0  100  100  100    0  100  100    0  100  
2021-10-08     0  100  100   34    0    0    1    0  100  
2021-10-11     0   35    0    0    0    0    0    0  100  
2021-10-12     0   34    0    0    0    0    0    0  100  
2021-10-13     0   34    0    0    0    0    0    0  100  
2021-10-14     0   34    0    0    0    0    0    0  100  
2021-10-15     0   35    0    0    0    0    0    0  100  
2021-10-18     0   34    0    0    0    0    0    0  100  
2021-10-19     0    0    0    0    0    0    0    0    0  
2021-10-20     0    0    0    0    0    0    0    0    0  
2021-10-21     0    0    0    0    0    0    0    0    0  
2021-10-22     0    0    0    0    0    0    0    0    0  
2021-10-25     0    0    0    0    0    0    0    0    0  
2021-10-26     0    0    0    0    0    0    0    0    0  
2021-10-27     0    0    0    0    0    0    0    0    0  
2021-10-28     0    0    0    0    0    0    0    0    0  
2021-10-29     0    0    0    0    0    0    0    0    0  
2021-11-01     0    0    0    0    0    0    0    0    0  
2021-11-02     0    0    0    0    0    0    0    0    0  
2021-11-03     0    0    0    0    0    0    0    0    0  
2021-11-04   

## TD3

Test TD3, predict

In [411]:
trained_model = trained_td3
df_account_value_td3, df_actions_td3 = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[1.00000000e+06 1.40653519e+02 1.95822250e+02 1.67727463e+02
  2.26000000e+02 1.83513992e+02 2.74900909e+02 5.07116776e+01
  9.38071213e+01 1.75438217e+02 3.52330719e+02 3.07771027e+02
  2.03622513e+02 1.20424385e+02 5.01258202e+01 1.48433197e+02
  1.54524490e+02 4.87658386e+01 2.28277725e+02 1.26340271e+02
  7.55181961e+01 2.82348145e+02 1.42315796e+02 1.30338394e+02
  1.43675705e+02 3.78985962e+02 2.25689667e+02 4.58676834e+01
  4.03038177e+01 4.38215256e+01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 1.44492004e+02
  2.15557999e+02 1.75300003e+02 2

Store graph of the value of portfolio

In [492]:
df_account_value_td3['date'] = pd.to_datetime(df_account_value_td3['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_td3['date'], df_account_value_td3['account_value'])

locator = mdates.MonthLocator(interval=1)  
plt.gca().xaxis.set_major_locator(locator)

formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for TD3')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/td3/testing/accountValue.png')
plt.close()


Trades made in testing

In [416]:
df_actions_td3.head(30)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS   GS  ...  MRK  \
date                                                            ...        
2021-10-01     0     0    0   0  100    0   100    0    0  100  ...    0   
2021-10-04     0     0    0   0  100    0   100    0    0  100  ...    0   
2021-10-05     0     0    0   0  100    0   100    0    0  100  ...    0   
2021-10-06     0     0    0   0  100    0   100    0    0  100  ...    0   
2021-10-07     0     0    0   0  100    0   100    0    0  100  ...    0   
2021-10-08     0     0    0   0  100    0   100    0    0  100  ...    0   
2021-10-11     0     0    0   0    1    0     0    0    0    0  ...    0   
2021-10-12     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-13     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-14     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-15     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-18     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-19     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-20     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-21     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-22     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-25     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-26     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-27     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-28     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-10-29     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-01     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-02     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-03     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-04     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-05     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-08     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-09     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-10     0     0    0   0    0    0     0    0    0    0  ...    0   
2021-11-11     0     0    0   0    0    0     0    0    0    0  ...    0   

            MSFT  NKE  PG  TRV  UNH    V  VZ  WBA  WMT  
date                                                    
2021-10-01     0    0   0    0    0  100   0    0    0  
2021-10-04     0    0   0    0    0  100   0    0    0  
2021-10-05     0    0   0    0    0  100   0    0    0  
2021-10-06     0    0   0    0    0  100   0    0    0  
2021-10-07     0    0   0    0    0  100   0    0    0  
2021-10-08     0    0   0    0    0  100   0    0    0  
2021-10-11     0    0   0    0    0    0   0    0    0  
2021-10-12     0    0   0    0    0    0   0    0    0  
2021-10-13     0    0   0    0    0    0   0    0    0  
2021-10-14     0    0   0    0    0    0   0    0    0  
2021-10-15     0    0   0    0    0    0   0    0    0  
2021-10-18     0    0   0    0    0    0   0    0    0  
2021-10-19     0    0   0    0    0    0   0    0    0  
2021-10-20     0    0   0    0    0    0   0    0    0  
2021-10-21     0    0   0    0    0    0   0    0    0  
2021-10-22     0    0   0    0    0    0   0    0    0  
2021-10-25     0    0   0    0    0    0   0    0    0  
2021-10-26     0    0   0    0    0    0   0    0    0  
2021-10-27     0    0   0    0    0    0   0    0    0  
2021-10-28     0    0   0    0    0    0   0    0    0  
2021-10-29     0    0   0    0    0    0   0    0    0  
2021-11-01     0    0   0    0    0    0   0    0    0  
2021-11-02     0    0   0    0    0    0   0    0    0  
2021-11-03     0    0   0    0    0    0   0    0    0  
2021-11-04     0    0   0    0    0    0   0    0    0  
2021-11-05     0    0   0    0    0    0

## SAC

Test SAC, predict

Account value is the DF that stores the history of the value of the assets (portfolio value) when used that algorithm

In [417]:
trained_model = trained_sac
df_account_value_sac, df_actions_sac = DRLAgent.DRL_prediction(
    model=trained_model, 
    environment = e_trade_gym)

el modelo es 
estos son los test obs
[[1.00000000e+06 1.40653519e+02 1.95822250e+02 1.67727463e+02
  2.26000000e+02 1.83513992e+02 2.74900909e+02 5.07116776e+01
  9.38071213e+01 1.75438217e+02 3.52330719e+02 3.07771027e+02
  2.03622513e+02 1.20424385e+02 5.01258202e+01 1.48433197e+02
  1.54524490e+02 4.87658386e+01 2.28277725e+02 1.26340271e+02
  7.55181961e+01 2.82348145e+02 1.42315796e+02 1.30338394e+02
  1.43675705e+02 3.78985962e+02 2.25689667e+02 4.58676834e+01
  4.03038177e+01 4.38215256e+01 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 0.00000000e+00
  0.00000000e+00 0.00000000e+00 0.00000000e+00 1.44492004e+02
  2.15557999e+02 1.75300003e+02 2

Store graph of the value of portfolio

In [493]:
df_account_value_sac['date'] = pd.to_datetime(df_account_value_sac['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_account_value_sac['date'], df_account_value_sac['account_value'])

locator = mdates.MonthLocator(interval=1)
plt.gca().xaxis.set_major_locator(locator)

formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

plt.gcf().autofmt_xdate()

plt.title('Account Value Testing for SAC')
plt.xlabel('Date')
plt.ylabel('Account Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/sac/testing/accountValue.png')
plt.close()


Trades made in testing

In [421]:
df_actions_sac.head(30)

AAPL  AMGN  AXP  BA  CAT  CRM  CSCO  CVX  DIS  GS  ...  MRK  MSFT  \
date                                                           ...              
2021-10-01     0    81   94   0    0   92     0   70   85  93  ...    0     0   
2021-10-04     0    81   94   0    0   92     0   70   85  93  ...    0     0   
2021-10-05     0    81   94   0    0   92     0   70   85  93  ...    0     0   
2021-10-06     0    81   94   0    0   92     0   70   85  93  ...    0     0   
2021-10-07     0     0   94   0    0    0     0    0    0  65  ...    0     0   
2021-10-08     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-11     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-12     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-13     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-14     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-15     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-18     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-19     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-20     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-21     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-22     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-25     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-26     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-27     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-28     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-10-29     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-01     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-02     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-03     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-04     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-05     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-08     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-09     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-10     0     0    0   0    0    0     0    0    0   0  ...    0     0   
2021-11-11     0     0    0   0    0    0     0    0    0   0  ...    0     0   

            NKE  PG  TRV  UNH  V  VZ  WBA  WMT  
date                                            
2021-10-01   89   5    0   82  0  51   89    0  
2021-10-04   89   5    0   82  0  51   89    0  
2021-10-05   89   5    0   82  0  51   89    0  
2021-10-06   89   5    0   82  0  51   89    0  
2021-10-07    0   0    0    0  0   0    1    0  
2021-10-08    0 -20    0    0  0   0   64    0  
2021-10-11    0   0    0    0  0   0    0    0  
2021-10-12    0   0    0    0  0   0    0    0  
2021-10-13    0   0    0    0  0   0    0    0  
2021-10-14    0   0    0    0  0   0    0    0  
2021-10-15    0   0    0    0  0   0    0    0  
2021-10-18    0   0    0    0  0   0    0    0  
2021-10-19    0   0    0    0  0   0    0    0  
2021-10-20    0   0    0    0  0   0    0    0  
2021-10-21    0   0    0    0  0   0    0    0  
2021-10-22    0   0    0    0  0   0    0    0  
2021-10-25    0   0    0    0  0   0    0    0  
2021-10-26    0   0    0    0  0   0    0    0  
2021-10-27    0   0    0    0  0   0    0    0  
2021-10-28    0   0    0    0  0   0    0    0  
2021-10-29    0   0    0    0  0   0    0    0  
2021-11-01    0   0    0    0  0   0    0    0  
2021-11-02    0   0    0    0  0   0    0    0  
2021-11-03    0   0    0    0  0   0    0    0  
2021-11-04    0   0    0    0  0   0    0    0  
2021-11-05    0   0    0    0  0   0    0    0  
2021-11-08    0   0    0    0  0   0    0    0 

Obtain results to then merge: merge in one DF the Portfolio Value given by each algorithm

In [494]:
df_result_a2c = df_account_value_a2c.set_index(df_account_value_a2c.columns[0])
df_result_a2c.rename(columns = {'account_value':'a2c'}, inplace = True)
df_result_ddpg = df_account_value_ddpg.set_index(df_account_value_ddpg.columns[0])
df_result_ddpg.rename(columns = {'account_value':'ddpg'}, inplace = True)
df_result_td3 = df_account_value_td3.set_index(df_account_value_td3.columns[0])
df_result_td3.rename(columns = {'account_value':'td3'}, inplace = True)
df_result_ppo = df_account_value_ppo.set_index(df_account_value_ppo.columns[0])
df_result_ppo.rename(columns = {'account_value':'ppo'}, inplace = True)
df_result_sac = df_account_value_sac.set_index(df_account_value_sac.columns[0])
df_result_sac.rename(columns = {'account_value':'sac'}, inplace = True)

We can also get stats from each stock individually (even though the analysis won't focus on that)

The following are the statistics based on a Series of the daily profitability of the Dow Jones Industrial Average

In [495]:
#baseline stats

print("==============Get Baseline Stats===========")
print("==============Baseline Stats of Profitability from DJIA===========")
print("This is the real performance of the index")
df_dji_ = get_baseline(
        ticker="^DJI", 
        start = TEST_START_DATE,
        end = TEST_END_DATE)
stats = backtest_stats(df_dji_, value_col_name = 'close')

[*********************100%%**********************]  1 of 1 completed

==============Get Baseline Stats===========
==============Baseline Stats of Profitability from DJIA===========
This is the real performance of the index
Shape of DataFrame:  (354, 8)
Annual return         -0.034876
Cumulative returns    -0.048644
Annual volatility      0.181612
Sharpe ratio          -0.105351
Calmar ratio          -0.158953
Stability              0.280983
Max drawdown          -0.219408
Omega ratio            0.982546
Sortino ratio         -0.146974
Skew                        NaN
Kurtosis                    NaN
Tail ratio             0.970602
Daily value at risk   -0.022957
dtype: float64


get_baseline vuelve a fetchear los stocks de YahooFinance dadas esas fechas.

backtest_stats llama a get daily return y luego saca stats de esa Serie con metodo que pide:

    """
    Calculates various performance metrics of a strategy, for use in
    plotting.show_perf_stats.

    Parameters
    ----------
    returns : pd.Series
        Daily returns of the strategy, noncumulative.
         - See full explanation in tears.create_full_tear_sheet.
    factor_returns : pd.Series, optional
        Daily noncumulative returns of the benchmark factor to which betas are
        computed. Usually a benchmark such as market returns.
         - This is in the same style as returns.
         - If None, do not compute alpha, beta, and information ratio.
    positions : pd.DataFrame
        Daily net position values.
         - See full explanation in tears.create_full_tear_sheet.
    transactions : pd.DataFrame
        Prices and amounts of executed trades. One row per trade.
        - See full explanation in tears.create_full_tear_sheet.
    turnover_denom : str
        Either AGB or portfolio_value, default AGB.
        - See full explanation in txn.get_turnover.

    Returns
    -------
    pd.Series
        Performance metrics.
    """

We will compare the results with the profitability we would get if we would invest 1000000$ (the initial amount we had for the algorithms) in the DJIA and we would not touch it. We compute it by obtaining the daily profitability of the index and multiplying by the initial amount

get daily profitability * invested amount = portfolio value in case of investing 1000000$ on DJ and not touching it

In [496]:
df_dji = pd.DataFrame()
df_dji['date'] = df_account_value_a2c['date']
df_dji['account_value'] = df_dji_['close'] / df_dji_['close'][0] * env_kwargs["initial_amount"] # get daily profitability * invested amount = portfolio value in case of investing 1000000$ on DJ and not touching it
#df_dji.to_csv("df_dji.csv")
df_dji = df_dji.set_index(df_dji.columns[0])
#df_dji.to_csv("df_dji+.csv")

Plot and Save the Price performance of the index DJ

In [497]:
df_dji_['date'] = pd.to_datetime(df_dji_['date']).dt.normalize()
plt.figure(figsize=(14, 7))
plt.plot(df_dji_['date'], df_dji_['close'])

locator = mdates.MonthLocator(interval=1)  
plt.gca().xaxis.set_major_locator(locator)

formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

plt.gcf().autofmt_xdate()

plt.title('Price Evolution of DJ (during testing time)')
plt.xlabel('Date')
plt.ylabel('Price')
plt.grid(True)

plt.savefig(f'resultadosTFG/DJIAPrices.png')
plt.close()

Plot and Save Account performance when only investing initial amount at the beginning

In [ ]:
df_dji.index = pd.to_datetime(df_dji.index)
plt.figure(figsize=(14, 7))
plt.plot(df_dji.index, df_dji['account_value'])

locator = mdates.MonthLocator(interval=1) 
plt.gca().xaxis.set_major_locator(locator)

formatter = mdates.DateFormatter('%Y-%m-%d')
plt.gca().xaxis.set_major_formatter(formatter)

plt.gcf().autofmt_xdate()

plt.title('Account Value Evolution of DJ (during testing time) with initial amount only')
plt.xlabel('Date')
plt.ylabel('Value')
plt.grid(True)

plt.savefig(f'resultadosTFG/DJIAAccountValue.png')
plt.close()

In [443]:
df_dji

account_value
date                     
2021-10-01   1.000000e+06
2021-10-04   9.905746e+05
2021-10-05   9.996566e+05
2021-10-06   1.002637e+06
2021-10-07   1.012483e+06
...                   ...
2023-02-21   9.651327e+05
2023-02-22   9.626710e+05
2023-02-23   9.658412e+05
2023-02-24   9.560240e+05
2023-02-27   9.581264e+05

[353 rows x 1 columns]

In [501]:
df_dji.rename(columns = {'account_value':'dji'}, inplace = True)

In [481]:
df_result_td3

td3
date                    
2021-10-01  1.000000e+06
2021-10-04  9.980908e+05
2021-10-05  1.001323e+06
2021-10-06  1.003328e+06
2021-10-07  1.011390e+06
...                  ...
2023-02-21  1.002243e+06
2023-02-22  9.993837e+05
2023-02-23  1.002683e+06
2023-02-24  9.949094e+05
2023-02-27  9.990868e+05

[353 rows x 1 columns]

Compare DJIA with the rest of the algorithms

In [502]:
result = pd.DataFrame()
result = pd.merge(result, df_result_a2c, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_ddpg, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_td3, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_ppo, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_result_sac, how='outer', left_index=True, right_index=True)
result = pd.merge(result, df_dji, how='outer', left_index=True, right_index=True)
display(result)

a2c          ddpg           td3           ppo  \
date                                                                 
2021-10-01  1.000000e+06  1.000000e+06  1.000000e+06  1.000000e+06   
2021-10-04  9.985967e+05  9.981534e+05  9.980908e+05  9.997712e+05   
2021-10-05  1.001278e+06  1.002404e+06  1.001323e+06  1.000228e+06   
2021-10-06  1.002252e+06  1.003774e+06  1.003328e+06  1.000330e+06   
2021-10-07  1.011794e+06  1.010930e+06  1.011390e+06  1.002330e+06   
...                  ...           ...           ...           ...   
2023-02-21  9.983648e+05  9.661120e+05  1.002243e+06  1.110605e+06   
2023-02-22  9.963950e+05  9.643979e+05  9.993837e+05  1.100560e+06   
2023-02-23  1.000296e+06  9.667462e+05  1.002683e+06  1.103351e+06   
2023-02-24  9.916845e+05  9.581022e+05  9.949094e+05  1.101601e+06   
2023-02-27  9.962109e+05  9.609648e+05  9.990868e+05  1.112850e+06   

                     sac           dji  
date                                    
2021-10-01  1.000000e+06  1.000000e+06  
2021-10-04  9.975824e+05  9.905746e+05  
2021-10-05  1.002473e+06  9.996566e+05  
2021-10-06  1.003407e+06  1.002637e+06  
2021-10-07  1.011903e+06  1.012483e+06  
...                  ...           ...  
2023-02-21  9.488691e+05  9.651327e+05  
2023-02-22  9.473324e+05  9.626710e+05  
2023-02-23  9.514772e+05  9.658412e+05  
2023-02-24  9.434197e+05  9.560240e+05  
2023-02-27  9.438514e+05  9.581264e+05  

[353 rows x 6 columns]

Save and Plot!

In [503]:
plt.rcParams["figure.figsize"] = (15,5)
plt.figure();
result.plot();
plt.savefig(f'resultadosTFG/AlgorithmsVsDJI.png')
plt.close()